## A workbook companion to the introduction to the DataFrames.jl package

*version: 2020-05-23* for DataFrames v0.21.1 and Julia v1.4.1

[Bogumił Kamiński](http://bogumilkaminski.pl/about/)

## Getting ready

We will use [this](http://archive.ics.uci.edu/ml/datasets/communities+and+crime) dataset. So first we download the required files.

In [1]:
using DataFrames
using CSV
using FreqTables
using Plots, StatsPlots
using GLM
using Statistics

You could also consider installing https://github.com/JuliaStats/StatsKit.jl package, but we want to be explicit what we use.

In [9]:
ENV["COLUMNS"] = 300
ENV["LINES"] = 20

20

## Loading the data

Here we have to do some non-standard operations.

In [2]:
colnamelines = filter(line -> startswith(line, "@attribute"), readlines("meta.txt"))

128-element Array{String,1}:
 "@attribute state numeric"
 "@attribute county numeric"
 "@attribute community numeric"
 "@attribute communityname string"
 "@attribute fold numeric"
 "@attribute population numeric"
 "@attribute householdsize numeric"
 "@attribute racepctblack numeric"
 "@attribute racePctWhite numeric"
 "@attribute racePctAsian numeric"
 "@attribute racePctHisp numeric"
 "@attribute agePct12t21 numeric"
 "@attribute agePct12t29 numeric"
 ⋮
 "@attribute NumKindsDrugsSeiz numeric"
 "@attribute PolicAveOTWorked numeric"
 "@attribute LandArea numeric"
 "@attribute PopDens numeric"
 "@attribute PctUsePubTrans numeric"
 "@attribute PolicCars numeric"
 "@attribute PolicOperBudg numeric"
 "@attribute LemasPctPolicOnPatr numeric"
 "@attribute LemasGangUnitDeploy numeric"
 "@attribute LemasPctOfficDrugUn numeric"
 "@attribute PolicBudgPerPop numeric"
 "@attribute ViolentCrimesPerPop numeric"

We need to convert column names to `Symbol` as this is the type that CSV.jl expects.

In [6]:
colnames = Symbol.(getindex.(split.(colnamelines), 2))

128-element Array{Symbol,1}:
 :state
 :county
 :community
 :communityname
 :fold
 :population
 :householdsize
 :racepctblack
 :racePctWhite
 :racePctAsian
 :racePctHisp
 :agePct12t21
 :agePct12t29
 ⋮
 :NumKindsDrugsSeiz
 :PolicAveOTWorked
 :LandArea
 :PopDens
 :PctUsePubTrans
 :PolicCars
 :PolicOperBudg
 :LemasPctPolicOnPatr
 :LemasGangUnitDeploy
 :LemasPctOfficDrugUn
 :PolicBudgPerPop
 :ViolentCrimesPerPop

In [4]:
coltypes = getindex.(split.(colnamelines), 3)

128-element Array{SubString{String},1}:
 "numeric"
 "numeric"
 "numeric"
 "string"
 "numeric"
 "numeric"
 "numeric"
 "numeric"
 "numeric"
 "numeric"
 "numeric"
 "numeric"
 "numeric"
 ⋮
 "numeric"
 "numeric"
 "numeric"
 "numeric"
 "numeric"
 "numeric"
 "numeric"
 "numeric"
 "numeric"
 "numeric"
 "numeric"
 "numeric"

In [7]:
df = CSV.File("data.txt", header=colnames) |> DataFrame

1994×128 DataFrame. Omitted printing of 122 columns
│ Row  │ state │ county │ community │ communityname       │ fold  │ population │
│      │ Int64 │ String │ String    │ String              │ Int64 │ Float64    │
├──────┼───────┼────────┼───────────┼─────────────────────┼───────┼────────────┤
│ 1    │ 8     │ ?      │ ?         │ Lakewoodcity        │ 1     │ 0.19       │
│ 2    │ 53    │ ?      │ ?         │ Tukwilacity         │ 1     │ 0.0        │
│ 3    │ 24    │ ?      │ ?         │ Aberdeentown        │ 1     │ 0.0        │
│ 4    │ 34    │ 5      │ 81440     │ Willingborotownship │ 1     │ 0.04       │
│ 5    │ 42    │ 95     │ 6096      │ Bethlehemtownship   │ 1     │ 0.01       │
│ 6    │ 6     │ ?      │ ?         │ SouthPasadenacity   │ 1     │ 0.02       │
│ 7    │ 44    │ 7      │ 41500     │ Lincolntown         │ 1     │ 0.01       │
│ 8    │ 6     │ ?      │ ?         │ Selmacity           │ 1     │ 0.01       │
│ 9    │ 21    │ ?      │ ?         │ Hendersoncity       │ 1     │ 0.03       │
│ 10   │ 29    │ ?      │ ?         │ Claytoncity         │ 1     │ 0.01       │
⋮
│ 1984 │ 13    │ ?      │ ?         │ ForestParkcity      │ 10    │ 0.01       │
│ 1985 │ 39    │ 95     │ 48342     │ Maumeecity          │ 10    │ 0.01       │
│ 1986 │ 1     │ ?      │ ?         │ AlexanderCitycity   │ 10    │ 0.01       │
│ 1987 │ 9     │ 3      │ 70550     │ Southingtontown     │ 10    │ 0.05       │
│ 1988 │ 44    │ 7      │ 11800     │ Burrillvilletown    │ 10    │ 0.01       │
│ 1989 │ 28    │ ?      │ ?         │ Columbuscity        │ 10    │ 0.02       │
│ 1990 │ 12    │ ?      │ ?         │ TempleTerracecity   │ 10    │ 0.01       │
│ 1991 │ 6     │ ?      │ ?         │ Seasidecity         │ 10    │ 0.05       │
│ 1992 │ 9     │ 9      │ 80070     │ Waterburytown       │ 10    │ 0.16       │
│ 1993 │ 25    │ 17     │ 72600     │ Walthamcity         │ 10    │ 0.08       │
│ 1994 │ 6     │ ?      │ ?         │ Ontariocity         │ 10    │ 0.2        │

We see that theere is a problem that `?` indicates a missing value in the data set

In [10]:
df = CSV.File("data.txt", header=colnames, missingstring="?") |> DataFrame

1994×128 DataFrame. Omitted printing of 106 columns
│ Row  │ state │ county  │ community │ communityname       │ fold  │ population │ householdsize │ racepctblack │ racePctWhite │ racePctAsian │ racePctHisp │ agePct12t21 │ agePct12t29 │ agePct16t24 │ agePct65up │ numbUrban │ pctUrban │ medIncome │ pctWWage │ pctWFarmSelf │ pctWInvInc │ pctWSocSec │
│      │ Int64 │ Int64?  │ Int64?    │ String              │ Int64 │ Float64    │ Float64       │ Float64      │ Float64      │ Float64      │ Float64     │ Float64     │ Float64     │ Float64     │ Float64    │ Float64   │ Float64  │ Float64   │ Float64  │ Float64      │ Float64    │ Float64    │
├──────┼───────┼─────────┼───────────┼─────────────────────┼───────┼────────────┼───────────────┼──────────────┼──────────────┼──────────────┼─────────────┼─────────────┼─────────────┼─────────────┼────────────┼───────────┼──────────┼───────────┼──────────┼──────────────┼────────────┼────────────┤
│ 1    │ 8     │ missing │ missing   │ Lakewoodcity        │ 1     │ 0.19       │ 0.33          │ 0.02         │ 0.9          │ 0.12         │ 0.17        │ 0.34        │ 0.47        │ 0.29        │ 0.32       │ 0.2       │ 1.0      │ 0.37      │ 0.72     │ 0.34         │ 0.6        │ 0.29       │
│ 2    │ 53    │ missing │ missing   │ Tukwilacity         │ 1     │ 0.0        │ 0.16          │ 0.12         │ 0.74         │ 0.45         │ 0.07        │ 0.26        │ 0.59        │ 0.35        │ 0.27       │ 0.02      │ 1.0      │ 0.31      │ 0.72     │ 0.11         │ 0.45       │ 0.25       │
│ 3    │ 24    │ missing │ missing   │ Aberdeentown        │ 1     │ 0.0        │ 0.42          │ 0.49         │ 0.56         │ 0.17         │ 0.04        │ 0.39        │ 0.47        │ 0.28        │ 0.32       │ 0.0       │ 0.0      │ 0.3       │ 0.58     │ 0.19         │ 0.39       │ 0.38       │
│ 4    │ 34    │ 5       │ 81440     │ Willingborotownship │ 1     │ 0.04       │ 0.77          │ 1.0          │ 0.08         │ 0.12         │ 0.1         │ 0.51        │ 0.5         │ 0.34        │ 0.21       │ 0.06      │ 1.0      │ 0.58      │ 0.89     │ 0.21         │ 0.43       │ 0.36       │
│ 5    │ 42    │ 95      │ 6096      │ Bethlehemtownship   │ 1     │ 0.01       │ 0.55          │ 0.02         │ 0.95         │ 0.09         │ 0.05        │ 0.38        │ 0.38        │ 0.23        │ 0.36       │ 0.02      │ 0.9      │ 0.5       │ 0.72     │ 0.16         │ 0.68       │ 0.44       │
⋮
│ 1989 │ 28    │ missing │ missing   │ Columbuscity        │ 10    │ 0.02       │ 0.41          │ 1.0          │ 0.21         │ 0.02         │ 0.01        │ 0.54        │ 0.57        │ 0.43        │ 0.45       │ 0.0       │ 0.0      │ 0.12      │ 0.37     │ 0.22         │ 0.27       │ 0.6        │
│ 1990 │ 12    │ missing │ missing   │ TempleTerracecity   │ 10    │ 0.01       │ 0.4           │ 0.1          │ 0.87         │ 0.12         │ 0.16        │ 0.43        │ 0.51        │ 0.35        │ 0.3        │ 0.03      │ 1.0      │ 0.42      │ 0.74     │ 0.14         │ 0.64       │ 0.3        │
│ 1991 │ 6     │ missing │ missing   │ Seasidecity         │ 10    │ 0.05       │ 0.96          │ 0.46         │ 0.28         │ 0.83         │ 0.32        │ 0.69        │ 0.86        │ 0.73        │ 0.14       │ 0.06      │ 1.0      │ 0.28      │ 0.76     │ 0.1          │ 0.3        │ 0.26       │
│ 1992 │ 9     │ 9       │ 80070     │ Waterburytown       │ 10    │ 0.16       │ 0.37          │ 0.25         │ 0.69         │ 0.04         │ 0.25        │ 0.35        │ 0.5         │ 0.31        │ 0.54       │ 0.17      │ 1.0      │ 0.31      │ 0.47     │ 0.17         │ 0.45       │ 0.58       │
│ 1993 │ 25    │ 17      │ 72600     │ Walthamcity         │ 10    │ 0.08       │ 0.51          │ 0.06         │ 0.87         │ 0.22         │ 0.1         │ 0.58        │ 0.74        │ 0.63        │ 0.41       │ 0.09      │ 1.0      │ 0.44      │ 0.64     │ 0.21         │ 0.55       │ 0.42       │
│ 1994 │ 6     │ missing │ missing   │ Ontariocity         

Let us check if what we detected is consistent with the metadata

In [11]:
freqtable(eltype.(eachcol(df)), coltypes)

5×2 Named Array{Int64,2}
            Dim1 ╲ Dim2 │ "numeric"   "string"
────────────────────────┼─────────────────────
Float64                 │       100          0
Union{Missing, Int64}   │         2          0
String                  │         0          1
Union{Missing, Float64} │        23          0
Int64                   │         2          0

In [12]:
describe(df)

128×8 DataFrame
│ Row │ variable            │ mean      │ min          │ median  │ max            │ nunique │ nmissing │ eltype                  │
│     │ Symbol              │ Union…    │ Any          │ Union…  │ Any            │ Union…  │ Union…   │ Type                    │
├─────┼─────────────────────┼───────────┼──────────────┼─────────┼────────────────┼─────────┼──────────┼─────────────────────────┤
│ 1   │ state               │ 28.6836   │ 1            │ 34.0    │ 56             │         │          │ Int64                   │
│ 2   │ county              │ 58.8268   │ 1            │ 23.0    │ 840            │         │ 1174     │ Union{Missing, Int64}   │
│ 3   │ community           │ 46188.3   │ 70           │ 48090.0 │ 94597          │         │ 1177     │ Union{Missing, Int64}   │
│ 4   │ communityname       │           │ Aberdeencity │         │ Zanesvillecity │ 1828    │          │ String                  │
│ 5   │ fold                │ 5.49398   │ 1            │ 5.0     │ 10             │         │          │ Int64                   │
⋮
│ 123 │ PolicOperBudg       │ 0.0767085 │ 0.0          │ 0.03    │ 1.0            │         │ 1675     │ Union{Missing, Float64} │
│ 124 │ LemasPctPolicOnPatr │ 0.698589  │ 0.0          │ 0.75    │ 1.0            │         │ 1675     │ Union{Missing, Float64} │
│ 125 │ LemasGangUnitDeploy │ 0.440439  │ 0.0          │ 0.5     │ 1.0            │         │ 1675     │ Union{Missing, Float64} │
│ 126 │ LemasPctOfficDrugUn │ 0.0940522 │ 0.0          │ 0.0     │ 1.0            │         │          │ Float64                 │
│ 127 │ PolicBudgPerPop     │ 0.195078  │ 0.0          │ 0.15    │ 1.0            │         │ 1675     │ Union{Missing, Float64} │
│ 128 │ ViolentCrimesPerPop │ 0.237979  │ 0.0          │ 0.15    │ 1.0            │         │          │ Float64                 │

## Analyzing the data

We will not want to use the first five columns from the data set. Let us get rid of them. This will be an in-place operation.

In [13]:
select!(df, Not(1:5))

1994×123 DataFrame. Omitted printing of 102 columns
│ Row  │ population │ householdsize │ racepctblack │ racePctWhite │ racePctAsian │ racePctHisp │ agePct12t21 │ agePct12t29 │ agePct16t24 │ agePct65up │ numbUrban │ pctUrban │ medIncome │ pctWWage │ pctWFarmSelf │ pctWInvInc │ pctWSocSec │ pctWPubAsst │ pctWRetire │ medFamInc │ perCapInc │
│      │ Float64    │ Float64       │ Float64      │ Float64      │ Float64      │ Float64     │ Float64     │ Float64     │ Float64     │ Float64    │ Float64   │ Float64  │ Float64   │ Float64  │ Float64      │ Float64    │ Float64    │ Float64     │ Float64    │ Float64   │ Float64   │
├──────┼────────────┼───────────────┼──────────────┼──────────────┼──────────────┼─────────────┼─────────────┼─────────────┼─────────────┼────────────┼───────────┼──────────┼───────────┼──────────┼──────────────┼────────────┼────────────┼─────────────┼────────────┼───────────┼───────────┤
│ 1    │ 0.19       │ 0.33          │ 0.02         │ 0.9          │ 0.12         │ 0.17        │ 0.34        │ 0.47        │ 0.29        │ 0.32       │ 0.2       │ 1.0      │ 0.37      │ 0.72     │ 0.34         │ 0.6        │ 0.29       │ 0.15        │ 0.43       │ 0.39      │ 0.4       │
│ 2    │ 0.0        │ 0.16          │ 0.12         │ 0.74         │ 0.45         │ 0.07        │ 0.26        │ 0.59        │ 0.35        │ 0.27       │ 0.02      │ 1.0      │ 0.31      │ 0.72     │ 0.11         │ 0.45       │ 0.25       │ 0.29        │ 0.39       │ 0.29      │ 0.37      │
│ 3    │ 0.0        │ 0.42          │ 0.49         │ 0.56         │ 0.17         │ 0.04        │ 0.39        │ 0.47        │ 0.28        │ 0.32       │ 0.0       │ 0.0      │ 0.3       │ 0.58     │ 0.19         │ 0.39       │ 0.38       │ 0.4         │ 0.84       │ 0.28      │ 0.27      │
│ 4    │ 0.04       │ 0.77          │ 1.0          │ 0.08         │ 0.12         │ 0.1         │ 0.51        │ 0.5         │ 0.34        │ 0.21       │ 0.06      │ 1.0      │ 0.58      │ 0.89     │ 0.21         │ 0.43       │ 0.36       │ 0.2         │ 0.82       │ 0.51      │ 0.36      │
│ 5    │ 0.01       │ 0.55          │ 0.02         │ 0.95         │ 0.09         │ 0.05        │ 0.38        │ 0.38        │ 0.23        │ 0.36       │ 0.02      │ 0.9      │ 0.5       │ 0.72     │ 0.16         │ 0.68       │ 0.44       │ 0.11        │ 0.71       │ 0.46      │ 0.43      │
⋮
│ 1989 │ 0.02       │ 0.41          │ 1.0          │ 0.21         │ 0.02         │ 0.01        │ 0.54        │ 0.57        │ 0.43        │ 0.45       │ 0.0       │ 0.0      │ 0.12      │ 0.37     │ 0.22         │ 0.27       │ 0.6        │ 0.83        │ 0.4        │ 0.15      │ 0.17      │
│ 1990 │ 0.01       │ 0.4           │ 0.1          │ 0.87         │ 0.12         │ 0.16        │ 0.43        │ 0.51        │ 0.35        │ 0.3        │ 0.03      │ 1.0      │ 0.42      │ 0.74     │ 0.14         │ 0.64       │ 0.3        │ 0.06        │ 0.46       │ 0.41      │ 0.49      │
│ 1991 │ 0.05       │ 0.96          │ 0.46         │ 0.28         │ 0.83         │ 0.32        │ 0.69        │ 0.86        │ 0.73        │ 0.14       │ 0.06      │ 1.0      │ 0.28      │ 0.76     │ 0.1          │ 0.3        │ 0.26       │ 0.37        │ 0.48       │ 0.24      │ 0.18      │
│ 1992 │ 0.16       │ 0.37          │ 0.25         │ 0.69         │ 0.04         │ 0.25        │ 0.35        │ 0.5         │ 0.31        │ 0.54       │ 0.17      │ 1.0      │ 0.31      │ 0.47     │ 0.17         │ 0.45       │ 0.58       │ 0.48        │ 0.57       │ 0.35      │ 0.31      │
│ 1993 │ 0.08       │ 0.51          │ 0.06         │ 0.87         │ 0.22         │ 0.1         │ 0.58        │ 0.74        │ 0.63        │ 0.41       │ 0.09      │ 1.0      │ 0.44      │ 0.64     │ 0.21         │ 0.55       │ 0.42       │ 0.24        │ 0.45       │ 0.47      │ 0.4       │
│ 1994 │ 0.2        │ 0.78          │ 0.14         │ 0.46         │ 0.24         │ 0.77        │ 0.5         │ 0.62        │ 0.4         │ 0.17       │ 0.21      │ 1.0      │ 0

Analyzing the correlation between `:ViolentCrimesPerProp` and other variables.

The challenge is that some of the variables have missing data and other do not have them. We want to use pairwise complete observations approach (delete only what we have to delete when calculating the correlation).

This will be our fisrst encounter with views of a `DataFrame`. The use of `@view` avoids copying of the data. This improves the performance, but in general you should not mutate the view, as the changes will propagate back to the parent.

In [15]:
results = DataFrame()
for col in names(df, Not("ViolentCrimesPerPop"))
    cols = [col, "ViolentCrimesPerPop"]
    subdf = @view df[completecases(df, cols), cols]
    push!(results, (vairable=col, correlation=cor(subdf[!, 1], subdf[!, 2])))
end

In [16]:
results

122×2 DataFrame
│ Row │ vairable            │ correlation │
│     │ String              │ Float64     │
├─────┼─────────────────────┼─────────────┤
│ 1   │ population          │ 0.367157    │
│ 2   │ householdsize       │ -0.0349226  │
│ 3   │ racepctblack        │ 0.631264    │
│ 4   │ racePctWhite        │ -0.68477    │
│ 5   │ racePctAsian        │ 0.0376218   │
⋮
│ 117 │ PolicCars           │ 0.381742    │
│ 118 │ PolicOperBudg       │ 0.33819     │
│ 119 │ LemasPctPolicOnPatr │ -0.082317   │
│ 120 │ LemasGangUnitDeploy │ 0.116163    │
│ 121 │ LemasPctOfficDrugUn │ 0.348627    │
│ 122 │ PolicBudgPerPop     │ 0.0959612   │

What if we want to see the most correlated values on top of the data frame?

In [17]:
sort!(results, :correlation, by = abs, rev=true)

122×2 DataFrame
│ Row │ vairable            │ correlation │
│     │ String              │ Float64     │
├─────┼─────────────────────┼─────────────┤
│ 1   │ PctKids2Par         │ -0.738424   │
│ 2   │ PctIlleg            │ 0.737957    │
│ 3   │ PctFam2Par          │ -0.706667   │
│ 4   │ racePctWhite        │ -0.68477    │
│ 5   │ PctYoungKids2Par    │ -0.666059   │
⋮
│ 117 │ racePctAsian        │ 0.0376218   │
│ 118 │ householdsize       │ -0.0349226  │
│ 119 │ PolicAveOTWorked    │ 0.0336298   │
│ 120 │ PctWorkMomYoungKids │ -0.0225354  │
│ 121 │ PctVacMore6Mos      │ 0.0212828   │
│ 122 │ PctSameState85      │ -0.0194589  │

Now let us do some additional analyses.

In [19]:
@df select(df, [results[1:4, 1]; "ViolentCrimesPerPop"]) corrplot(cols(1:5))

In [20]:
lm(@formula(ViolentCrimesPerPop ~ PctKids2Par + PctIlleg + racePctWhite), df)

StatsModels.TableRegressionModel{LinearModel{GLM.LmResp{Array{Float64,1}},GLM.DensePredChol{Float64,LinearAlgebra.Cholesky{Float64,Array{Float64,2}}}},Array{Float64,2}}

ViolentCrimesPerPop ~ 1 + PctKids2Par + PctIlleg + racePctWhite

Coefficients:
─────────────────────────────────────────────────────────────────────────────
               Estimate  Std. Error   t value  Pr(>|t|)  Lower 95%  Upper 95%
─────────────────────────────────────────────────────────────────────────────
(Intercept)    0.649797   0.0343578   18.9126    <1e-72   0.582416   0.717178
PctKids2Par   -0.444269   0.0322473  -13.7769    <1e-40  -0.507511  -0.381027
PctIlleg       0.192406   0.0346147    5.5585    <1e-7    0.124521   0.260291
racePctWhite  -0.244363   0.0225653  -10.8291    <1e-25  -0.288617  -0.200108
─────────────────────────────────────────────────────────────────────────────

Now feel free to experiment with the data set.